Some Observations

In [108]:
import pandas as pd
import numpy as np
import matplotlib as mp
import sklearn as sk
import plotly
import plotly.graph_objs as go
import plotly.offline as offline
from plotly.graph_objs import *
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected=True)

In [109]:
url = 'https://raw.githubusercontent.com/uw-covid-hackathon/covid-visualization/master/OXFORD_latest_daily_columns.csv'
latest_csv = pd.read_csv(url, error_bad_lines=False)
latest_csv.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 28793 entries, 0 to 28792
Data columns (total 44 columns):
 #   Column                                 Non-Null Count  Dtype  
---  ------                                 --------------  -----  
 0   CountryName                            28793 non-null  object 
 1   Date                                   28793 non-null  object 
 2   CountryCode                            28793 non-null  object 
 3   C1_School closing                      27937 non-null  float64
 4   C1_Flag                                14559 non-null  float64
 5   C2_Workplace closing                   27891 non-null  float64
 6   C2_Flag                                13040 non-null  float64
 7   C3_Cancel public events                27894 non-null  float64
 8   C3_Flag                                14925 non-null  float64
 9   C4_Restrictions on gatherings          27900 non-null  float64
 10  C4_Flag                                13123 non-null  float64
 11  C5

In [110]:
df = latest_csv[['CountryName', 'Date', 'ConfirmedCases', 'ConfirmedDeaths', 'NewConfirmedCases']]

In [111]:
import plotly.express as px
fig = px.line(df, x="Date", y="NewConfirmedCases", color="CountryName",
              line_group="CountryName", hover_name="CountryName")
fig.show()
fig = px.line(df, x="Date", y="ConfirmedCases", color="CountryName",
              line_group="CountryName", hover_name="CountryName")
fig.show()

# World View - Viz 2

In [112]:
url = 'https://raw.githubusercontent.com/uw-covid-hackathon/covid-visualization/master/OXFORD_latest_daily_columns.csv'
latest_csv = pd.read_csv(url, error_bad_lines=False)
latest_csv.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 28793 entries, 0 to 28792
Data columns (total 44 columns):
 #   Column                                 Non-Null Count  Dtype  
---  ------                                 --------------  -----  
 0   CountryName                            28793 non-null  object 
 1   Date                                   28793 non-null  object 
 2   CountryCode                            28793 non-null  object 
 3   C1_School closing                      27937 non-null  float64
 4   C1_Flag                                14559 non-null  float64
 5   C2_Workplace closing                   27891 non-null  float64
 6   C2_Flag                                13040 non-null  float64
 7   C3_Cancel public events                27894 non-null  float64
 8   C3_Flag                                14925 non-null  float64
 9   C4_Restrictions on gatherings          27900 non-null  float64
 10  C4_Flag                                13123 non-null  float64
 11  C5

In [113]:
df_c = latest_csv[['Date', 'ConfirmedCases','ConfirmedDeaths', 'NewConfirmedCases', 'NewConfirmedDeaths']]
df_w = pd.DataFrame()
df_w['WorldCases'] = df_c.groupby(['Date'])['ConfirmedCases'].sum()
df_w['WorldDeaths'] = df_c.groupby(['Date'])['ConfirmedDeaths'].sum()
df_w['WorldCases_Day'] = df_c.groupby(['Date'])['NewConfirmedCases'].sum()
df_w['WorldDeaths_Day'] = df_c.groupby(['Date'])['NewConfirmedDeaths'].sum()
df_w = df_w.reset_index()
df_w.info()     

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 165 entries, 0 to 164
Data columns (total 5 columns):
 #   Column           Non-Null Count  Dtype  
---  ------           --------------  -----  
 0   Date             165 non-null    object 
 1   WorldCases       165 non-null    int64  
 2   WorldDeaths      165 non-null    int64  
 3   WorldCases_Day   165 non-null    float64
 4   WorldDeaths_Day  165 non-null    float64
dtypes: float64(2), int64(2), object(1)
memory usage: 6.6+ KB


# Cumulative COVID Deaths and Cases + COVID Deaths ad Cases per Day

In [114]:
# import plotly.express as px
fig = go.Figure()

#Cases
fig.add_trace(go.Scatter(x=df_w['Date'], y=df_w['WorldCases'], name='Cases',  visible=True,
                         line=dict(color='firebrick', width=3)))

fig.add_trace(go.Scatter(x=df_w['Date'], y=df_w['WorldCases_Day'], name='Cases Per Day', visible = False,
                         line=dict(color='firebrick', width=3)))

#Deaths
fig.add_trace(go.Scatter(x=df_w['Date'], y=df_w['WorldDeaths'], name = 'Deaths', visible=True,
                         line=dict(color='black', width=3)))

fig.add_trace(go.Scatter(x=df_w['Date'], y=df_w['WorldDeaths_Day'], name = 'Deaths Per Day', visible=False,
                         line=dict(color='black', width=3)))


cumulative = [dict(x=df_w['Date'], y=df_w['WorldCases'], name='Cumulative Confirmed Cases',
                         line=dict(color='firebrick', width=3)), dict(x=df_w['Date'], y=df_w['WorldDeaths'], name = 'Cumulative Confirmed Deaths',
                         line=dict(color='black', width=3))
         ]

per_day = [
                         dict(x=df_w['Date'], y=df_w['WorldCases_Day'], name='Cases Per Day', 
                         line=dict(color='firebrick', width=3)),
        dict(x=df_w['Date'], y=df_w['WorldDeaths_Day'], name = 'Deaths Per Day',
                         line=dict(color='black', width=3))]


fig.update_layout(
    updatemenus=[
        dict(
            active=0,
            buttons=list([
                dict(label="Cumulative",
                     method="update",
                     args=[{"visible": [True, False, True, False]},
                           {"title": "Cumulative COVID Deaths and Cases",
                            "annotations": cumulative}]),
                dict(label="Per Day",
                     method="update",
                     args=[{"visible": [False, True, False, True]},
                           {"title": "COVID Deaths and Cases per Day",
                            "annotations": per_day}]),
            ]),
        )
    ])

fig.update_layout(
    autosize=False,
    height=500, 
    width=1000, 
    title_text="Cumulative COVID Deaths and Cases"
)

fig.show()

In [118]:
plotly.offline.plot(fig)

'temp-plot.html'